In [1]:
import pandas as pd
df=pd.read_csv("EURUSD_Candlestick_5_M_ASK_30.09.2019-30.09.2022.csv")
df

Gmt time     Open     High      Low    Close   Volume
0       30.09.2019 00:00:00.000  1.09425  1.09426  1.09405  1.09406   585.10
1       30.09.2019 00:05:00.000  1.09408  1.09414  1.09401  1.09409   289.39
2       30.09.2019 00:10:00.000  1.09410  1.09423  1.09408  1.09410   276.24
3       30.09.2019 00:15:00.000  1.09409  1.09410  1.09388  1.09389   439.29
4       30.09.2019 00:20:00.000  1.09390  1.09395  1.09388  1.09395   341.23
...                         ...      ...      ...      ...      ...      ...
225081  30.09.2022 20:35:00.000  0.98028  0.98034  0.98001  0.98022   624.12
225082  30.09.2022 20:40:00.000  0.98023  0.98047  0.98007  0.98030   408.20
225083  30.09.2022 20:45:00.000  0.98026  0.98034  0.98019  0.98031   317.29
225084  30.09.2022 20:50:00.000  0.98031  0.98067  0.97987  0.97999  1472.13
225085  30.09.2022 20:55:00.000  0.98000  0.98066  0.97993  0.98026  1068.81

[225086 rows x 6 columns]

In [2]:
df["Gmt time"]=df["Gmt time"].str.replace(".000","")
df['Gmt time']=pd.to_datetime(df['Gmt time'],format='%d.%m.%Y %H:%M:%S')
df.set_index("Gmt time", inplace=True)
df=df[df.High!=df.Low]
len(df)

224989

In [35]:
import pandas_ta as ta
df["VWAP"] = ta.vwap(df.High, df.Low, df.Close, df.Volume).copy()  # Use .copy()
df['RSI'] = ta.rsi(df.Close, length=16).copy()  # Use .copy()

my_bbands = ta.bbands(df.Close, length=14, std=2.0)
df = df.join(my_bbands, rsuffix='_my_bbands')




In [36]:
VWAPsignal = [0]*len(df)
backcandles = 15

for row in range(backcandles, len(df)):
    upt = 1
    dnt = 1
    for i in range(row-backcandles, row+1):
        if max(df.Open[i], df.Close[i])>=df.VWAP[i]:
            dnt=0
        if min(df.Open[i], df.Close[i])<=df.VWAP[i]:
            upt=0
    if upt==1 and dnt==1:
        VWAPsignal[row]=3
    elif upt==1:
        VWAPsignal[row]=2
    elif dnt==1:
        VWAPsignal[row]=1

df['VWAPSignal'] = VWAPsignal

In [37]:
def TotalSignal(l):
    if (df.VWAPSignal[l]==2
        and df.Close[l]<=df['BBL_14_2.0'][l]
        and df.RSI[l]<45):
            return 2
    if (df.VWAPSignal[l]==1
        and df.Close[l]>=df['BBU_14_2.0'][l]
        and df.RSI[l]>55):
            return 1
    return 0
        
TotSignal = [0]*len(df)
for row in range(backcandles, len(df)): #careful backcandles used previous cell
    TotSignal[row] = TotalSignal(row)
df['TotalSignal'] = TotSignal

In [38]:
df[df.TotalSignal!=0].count()

Open                    2781
High                    2781
Low                     2781
Close                   2781
Volume                  2781
VWAP                    2781
RSI                     2781
BBL_14_2.0              2781
BBM_14_2.0              2781
BBU_14_2.0              2781
BBB_14_2.0              2781
BBP_14_2.0              2781
VWAPSignal              2781
TotalSignal             2781
pointposbreak           2781
BBL_14_2.0_my_bbands    2781
BBM_14_2.0_my_bbands    2781
BBU_14_2.0_my_bbands    2781
BBB_14_2.0_my_bbands    2781
BBP_14_2.0_my_bbands    2781
dtype: int64

In [39]:
import numpy as np
def pointposbreak(x):
    if x['TotalSignal']==1:
        return x['High']+1e-4
    elif x['TotalSignal']==2:
        return x['Low']-1e-4
    else:
        return np.nan

df['pointposbreak'] = df.apply(lambda row: pointposbreak(row), axis=1)

In [40]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from datetime import datetime
st=10400
dfpl = df[st:st+350]
dfpl.reset_index(inplace=True)
fig = go.Figure(data=[go.Candlestick(x=dfpl.index,
                open=dfpl['Open'],
                high=dfpl['High'],
                low=dfpl['Low'],
                close=dfpl['Close']),
                go.Scatter(x=dfpl.index, y=dfpl.VWAP, 
                           line=dict(color='blue', width=1), 
                           name="VWAP"), 
                go.Scatter(x=dfpl.index, y=dfpl['BBL_14_2.0'], 
                           line=dict(color='green', width=1), 
                           name="BBL"),
                go.Scatter(x=dfpl.index, y=dfpl['BBU_14_2.0'], 
                           line=dict(color='green', width=1), 
                           name="BBU")])

fig.add_scatter(x=dfpl.index, y=dfpl['pointposbreak'], mode="markers",
                marker=dict(size=10, color="MediumPurple"),
                name="Signal")
fig.show()

In [41]:
dfpl = df[:10000].copy()
import pandas_ta as ta
dfpl['ATR']=ta.atr(dfpl.High, dfpl.Low, dfpl.Close, length=7)
#help(ta.atr)
def SIGNAL():
    return dfpl.TotalSignal

In [42]:
from backtesting import Strategy
from backtesting import Backtest

class MyStrat(Strategy):
    initsize = 0.99
    mysize = initsize
    def init(self):
        super().init()
        self.signal1 = self.I(SIGNAL)

    def next(self):
        super().next()
        slatr = 1.2*self.data.ATR[-1]
        TPSLRatio = 1.5

        if len(self.trades)>0:
            if self.trades[-1].is_long and self.data.RSI[-1]>=90:
                self.trades[-1].close()
            elif self.trades[-1].is_short and self.data.RSI[-1]<=10:
                self.trades[-1].close()
        
        if self.signal1==2 and len(self.trades)==0:
            sl1 = self.data.Close[-1] - slatr
            tp1 = self.data.Close[-1] + slatr*TPSLRatio
            self.buy(sl=sl1, tp=tp1, size=self.mysize)
        
        elif self.signal1==1 and len(self.trades)==0:         
            sl1 = self.data.Close[-1] + slatr
            tp1 = self.data.Close[-1] - slatr*TPSLRatio
            self.sell(sl=sl1, tp=tp1, size=self.mysize)

bt = Backtest(dfpl, MyStrat, cash=100, margin=1/10, commission=0.00)
stat = bt.run()
stat

Start                     2019-09-30 00:00:00
End                       2019-11-15 18:20:00
Duration                     46 days 18:20:00
Exposure Time [%]                        5.98
Equity Final [$]                   108.196519
Equity Peak [$]                    108.196519
Return [%]                           8.196519
Buy & Hold Return [%]                 1.03742
Return (Ann.) [%]                   51.348548
Volatility (Ann.) [%]               12.727459
Sharpe Ratio                          4.03447
Sortino Ratio                       14.674265
Calmar Ratio                        21.383331
Max. Drawdown [%]                   -2.401335
Avg. Drawdown [%]                   -0.332501
Max. Drawdown Duration       13 days 18:35:00
Avg. Drawdown Duration        0 days 16:11:00
# Trades                                   75
Win Rate [%]                        53.333333
Best Trade [%]                       0.114888
Worst Trade [%]                      -0.07265
Avg. Trade [%]                    

In [49]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots

# Plot equity curve
fig = make_subplots(rows=2, cols=1, shared_xaxes=True)

# Add equity curve trace
equity_curve_trace = go.Scatter(x=stat.index, y=stat["_equity_curve"], mode="lines", name="Equity Curve")
fig.add_trace(equity_curve_trace, row=1, col=1)

# Add signals and indicators on the second row
for col, indicator in enumerate(['VWAP', 'BBL_14_2.0', 'BBU_14_2.0', 'pointposbreak']):
    indicator_trace = go.Scatter(x=dfpl.index, y=dfpl[indicator], mode="lines", name=indicator)
    fig.add_trace(indicator_trace, row=2, col=1)

# Customize layout
fig.update_layout(
    title="Backtest Results Visualization",
    xaxis_title="Date",
    yaxis_title="Value",
    xaxis_rangeslider_visible=False,
    showlegend=True
)

# Show the Plotly figure
fig.show()
